In [2]:
import esm
import torch
import time
import gc
import os
import numpy as np
from Bio import SeqIO

%run "../scripts/data_processing.py"
%run "../scripts/node_edge_generation.py"
%run "../scripts/graph_functions.py"

#Data path
datadir = os.path.abspath("../../Data/")

In [4]:
os.system("ls -ltr "+ datadir+"/GWAS/PRJNA1104541")

total 3336096
-rw-rw-r-- 1 louie louie  175829790 Sep 11 11:19 SRR28808366.fastq.gz
-rw-rw-r-- 1 louie louie 1018615597 Sep 11 14:37 SRR28808366.fastq
-rw-rw-r-- 1 louie louie 1198905186 Sep 14 11:46 SRR28808366_aligned.sam
-rw-rw-r-- 1 louie louie  105216016 Sep 14 14:29 SRR28808366_aligned.bam
-rw-rw-r-- 1 louie louie  913693927 Sep 15 09:51 SRR28808366.bcf
-rw-rw-r-- 1 louie louie    3873402 Sep 15 10:18 SRR28808366.vcf
-rw-rw-r-- 1 louie louie          0 Sep 15 20:28 SRR28808366_annotated.vcf


0

In [24]:
# Replace with your FASTQ file path
fastq_in = datadir+"/GWAS/PRJNA1104541/SRR28808366.fastq"
allseq = SeqIO.parse(fastq_in, "fastq")
print(len(list(allseq)))
for record in allseq:
    print("Read ID:", record.id)
    print("Sequence:", record.seq)
    print("Quality scores:", record.letter_annotations["phred_quality"])
    print("-" * 40)
    break

4868293


In [28]:
qualities = []
allseq = SeqIO.parse(fastq_in, "fastq")
for record in allseq:
    qualities.extend(record.letter_annotations["phred_quality"])

print("Average read quality:", np.mean(qualities))
print("Median read quality:", np.median(qualities))
print("Reads processed:", len(list(SeqIO.parse(fastq_in, "fastq"))))

Average read quality: 34.96622081493872
Median read quality: 37.0
Reads processed: 4868293


In [8]:
for i in os.listdir(datadir+"/GWAS/PRJNA1104541/"):
    if "fastq" in i and ".gz" not in i:
        print(i)

SRR28808386.fastq
SRR28808390.fastq
SRR28808376.fastq
SRR28808368.fastq
SRR28808366.fastq
SRR28808389.fastq
SRR28808392.fastq
SRR28808383.fastq
SRR28808381.fastq
SRR28808372.fastq
SRR28808388.fastq
SRR28808378.fastq
SRR28808393.fastq
SRR28808364.fastq
SRR28808369.fastq
SRR28808380.fastq
SRR28808374.fastq
SRR28808373.fastq
SRR28808385.fastq
SRR28808391.fastq
SRR28808379.fastq
SRR28808377.fastq
SRR28808370.fastq
SRR28808367.fastq
SRR28808365.fastq
SRR28808384.fastq
SRR28808371.fastq
SRR28808375.fastq
SRR28808382.fastq
SRR28808387.fastq


In [ ]:
#CLI tools

# Index the reference genome
#bwa index GCF_000001405.40_GRCh38.p14_genomic.fna
#Real time: 2458.246 sec; CPU: 2453.128 sec

# Align reads to reference (single-end example)
#bwa mem Hsapiens_ref/GCF_000001405.40_GRCh38.p14_genomic.fna PRJNA1104541/SRR28808366.fastq > SRR28808366_aligned.sam
#Real time: 1051.976 sec; CPU: 1052.014 sec

# Convert SAM to BAM
#samtools view -Sb SRR28808366_aligned.sam | samtools sort -o SRR28808366_aligned.bam

#Pileup generation
#bcftools mpileup -f ../Hsapiens_ref/GCF_000001405.40_GRCh38.p14_genomic.fna ./SRR28808366_aligned.bam > SRR28808366.bcf

# Call variants
#bcftools call -mv -Ov -o SRR28808366.vcf SRR28808366.bcf

# Annotate VCF
#java -Xmx4g -jar /home/louie/Documents/Software/snpEff/snpEff.jar GRCh38.99 SRR28808366.vcf > SRR28808366_annotated.vcf

In [3]:
from cyvcf2 import VCF

vcf = VCF(datadir+"/GWAS/PRJNA1104541/SRR28808366.vcf")

for variant in vcf:
    print("Chrom:", variant.CHROM)
    print("Pos:", variant.POS)
    print("Ref:", variant.REF)
    print("Alt:", variant.ALT)
    print("Qual:", variant.QUAL)
    print("Genotypes:", variant.genotypes)  # per-sample genotype calls
    print("-" * 30)


Chrom: NC_000001.11
Pos: 629180
Ref: A
Alt: ['T']
Qual: 5.928579807281494
Genotypes: [[1, 1, False]]
------------------------------
Chrom: NC_000001.11
Pos: 629216
Ref: A
Alt: ['G']
Qual: 6.7357001304626465
Genotypes: [[1, 1, False]]
------------------------------
Chrom: NC_000001.11
Pos: 629241
Ref: C
Alt: ['T']
Qual: 15.537300109863281
Genotypes: [[1, 1, False]]
------------------------------
Chrom: NC_000001.11
Pos: 944296
Ref: G
Alt: ['A']
Qual: 8.138689994812012
Genotypes: [[1, 1, False]]
------------------------------
Chrom: NC_000001.11
Pos: 944307
Ref: T
Alt: ['C']
Qual: 8.138689994812012
Genotypes: [[1, 1, False]]
------------------------------
Chrom: NC_000001.11
Pos: 944575
Ref: T
Alt: ['A']
Qual: 8.138689994812012
Genotypes: [[1, 1, False]]
------------------------------
Chrom: NC_000001.11
Pos: 965643
Ref: T
Alt: ['C']
Qual: 8.138689994812012
Genotypes: [[1, 1, False]]
------------------------------
Chrom: NC_000001.11
Pos: 975783
Ref: C
Alt: ['T']
Qual: 225.41700744628906

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)

